In [1]:
import pandas as pd
import numpy as np
import pickle
from sklearn.linear_model import LinearRegression
from sklearn.ensemble import RandomForestRegressor
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.grid_search import GridSearchCV

C:\Users\DELL\Anaconda3\lib\site-packages\sklearn\ensemble\weight_boosting.py:29: DeprecationWarning: numpy.core.umath_tests is an internal NumPy module and should not be imported. It will be removed in a future NumPy release.
  from numpy.core.umath_tests import inner1d
C:\Users\DELL\Anaconda3\lib\site-packages\sklearn\cross_validation.py:41: DeprecationWarning: This module was deprecated in version 0.18 in favor of the model_selection module into which all the refactored classes and functions are moved. Also note that the interface of the new CV iterators are different from that of this module. This module will be removed in 0.20.
  "This module will be removed in 0.20.", DeprecationWarning)
C:\Users\DELL\Anaconda3\lib\site-packages\sklearn\grid_search.py:42: DeprecationWarning: This module was deprecated in version 0.18 in favor of the model_selection module into which all the refactored classes and functions are moved. This module will be removed in 0.20.
  DeprecationWarning)


In [2]:
from openpyxl import Workbook,load_workbook

In [3]:
import os

In [4]:
from sklearn.metrics import r2_score,mean_squared_error,precision_score,recall_score,accuracy_score,confusion_matrix,roc_auc_score

In [5]:
os.chdir('../output_data')

In [6]:
df = pd.read_csv('train_v04.csv',header=0)

In [6]:
ignore_cols = ['Symbol','Series','Date','Prev_Close','Open','Close','Prev_Close_min','Prev_Close_max','Sector']

In [7]:
os.chdir('../pickles')

In [8]:
numerical = pickle.load(open('numerical.pickle','rb'))
categorical = pickle.load(open('categorical.pickle','rb'))
conversion_dict = pickle.load(open('conversion_dict.pickle','rb'))
imputation_cols = pickle.load(open('imputation_cols.pickle','rb'))
model_columns = pickle.load(open('model_columns.pickle','rb'))
lr_model_columns = pickle.load(open('lr_model_columns.pickle','rb'))
order = pickle.load(open('order.pickle','rb'))
pca = pickle.load(open('pca.pickle','rb'))
scale = pickle.load(open('scale.pickle','rb'))

In [9]:
from keras.layers import Input,Dense,Dropout

Using TensorFlow backend.


In [10]:
from keras.models import Model
from keras.optimizers import Adam,RMSprop

In [14]:
states = Input(shape=(165,))
x = Dense(units = 85, activation='linear')(states)
y = Dense(units = 85,activation='linear')(x)
q_value = Dense(units = 1,activation='sigmoid')(y)
ann_model = Model(inputs=states,outputs=q_value)
ann_model.compile(loss='binary_crossentropy',optimizer=Adam(lr=.001))

In [16]:
model_inputs = np.array(df.drop(ignore_cols+['actual_return','lift'],axis=1))
model_returns = np.array(df['lift'])

In [17]:
ann_model.fit(model_inputs,model_returns,epochs=100,batch_size=50)

Epoch 1/100
85799/85799 [==============================] - 17s 195us/step - loss: 0.6933
Epoch 2/100
85799/85799 [==============================] - 13s 157us/step - loss: 0.6905
Epoch 3/100
85799/85799 [==============================] - 14s 159us/step - loss: 0.6894
Epoch 4/100
85799/85799 [==============================] - 13s 157us/step - loss: 0.6889
Epoch 5/100
85799/85799 [==============================] - 14s 158us/step - loss: 0.6885
Epoch 6/100
85799/85799 [==============================] - 14s 166us/step - loss: 0.6883
Epoch 7/100
85799/85799 [==============================] - 14s 166us/step - loss: 0.68810
Epoch 8/100
85799/85799 [==============================] - 17s 197us/step - loss: 0.6879
Epoch 9/100
85799/85799 [==============================] - 14s 161us/step - loss: 0.6878
Epoch 10/100
85799/85799 [==============================] - 14s 162us/step - loss: 0.6877
Epoch 11/100
85799/85799 [==============================] - 14s 163us/step - loss: 0.6876
Epoch 12/100
85799

In [11]:
os.chdir('../Models/')

In [19]:
ann_model.save('ann_prob_model.h5')

In [12]:
from keras.models import load_model

In [13]:
model = load_model('ann_prob_model.h5')

In [23]:
pred_returns = [x[0] for x in model.predict(model_inputs)]

In [25]:
roc_auc_score(y_score=pred_returns,y_true=model_returns)

0.5632988203003302

In [26]:
df['lift_prob'] = pred_returns

In [29]:
buck_rows = df.shape[0]//100
stats_numerical = pd.DataFrame()
for col in ['lift_prob']:
    df_append = df.sort_values(by=col,ascending=False)
    df_append.reset_index(inplace=True)
    df_append['bucket'] = df_append.index//buck_rows
    df_stats = df_append.groupby('bucket').agg({col:['min','mean','max','count'],
                                               'lift':['sum']})
    df_stats.columns = df_stats.columns.droplevel()
    df_stats.columns = ['min_prob','mean_prob','max_prob','counts','lifts']
    df_stats.reset_index(inplace=True)
    stats_numerical = stats_numerical.append(df_stats)

In [30]:
stats_numerical

bucket  min_prob  mean_prob  max_prob  counts  lifts
0         0  0.588147   0.608967  0.685120     857    543
1         1  0.572210   0.579268  0.588136     857    488
2         2  0.563333   0.567335  0.572181     857    516
3         3  0.556550   0.559691  0.563326     857    509
4         4  0.551527   0.553918  0.556514     857    488
5         5  0.547332   0.549377  0.551525     857    489
6         6  0.543630   0.545377  0.547329     857    476
7         7  0.540363   0.541947  0.543612     857    481
8         8  0.537472   0.538908  0.540363     857    468
9         9  0.534843   0.536117  0.537467     857    462
10       10  0.532212   0.533513  0.534829     857    472
11       11  0.529855   0.531052  0.532210     857    459
12       12  0.527620   0.528729  0.529854     857    475
13       13  0.525499   0.526533  0.527619     857    456
14       14  0.523654   0.524602  0.525495     857    469
15       15  0.521846   0.522715  0.523654     857    468
16       16  0.520012   0.520911  0.521845     857    447
17       17  0.518327   0.519167  0.520011     857    451
18       18  0.516734   0.517523  0.518325     857    457
19       19  0.515151   0.515952  0.516733     857    442
20       20  0.513532   0.514322  0.515151     857    426
21       21  0.512000   0.512757  0.513530     857    431
22       22  0.510583   0.511276  0.511999     857    451
23       23  0.509095   0.509842  0.510582     857    450
24       24  0.507670   0.508365  0.509094     857    480
25       25  0.506283   0.506988  0.507669     857    401
26       26  0.504985   0.505625  0.506282     857    425
27       27  0.503658   0.504316  0.504983     857    420
28       28  0.502371   0.503033  0.503658     857    438
29       29  0.501043   0.501701  0.502370     857    435
..      ...       ...        ...       ...     ...    ...
71       71  0.453311   0.453885  0.454499     857    357
72       72  0.452057   0.452691  0.453304     857    383
73       73  0.450824   0.451462  0.452056     857    369
74       74  0.449474   0.450167  0.450824     857    363
75       75  0.448158   0.448830  0.449473     857    367
76       76  0.446820   0.447501  0.448157     857    367
77       77  0.445512   0.446158  0.446820     857    348
78       78  0.444086   0.444815  0.445511     857    333
79       79  0.442652   0.443370  0.444085     857    355
80       80  0.441115   0.441868  0.442649     857    358
81       81  0.439488   0.440323  0.441111     857    370
82       82  0.437807   0.438638  0.439487     857    368
83       83  0.436134   0.437003  0.437805     857    323
84       84  0.434276   0.435209  0.436133     857    350
85       85  0.432478   0.433380  0.434273     857    333
86       86  0.430495   0.431534  0.432477     857    354
87       87  0.428447   0.429472  0.430494     857    324
88       88  0.426207   0.427339  0.428446     857    341
89       89  0.423903   0.425121  0.426206     857    352
90       90  0.421428   0.422711  0.423902     857    342
91       91  0.418843   0.420148  0.421425     857    358
92       92  0.415899   0.417366  0.418842     857    368
93       93  0.412587   0.414283  0.415895     857    345
94       94  0.408735   0.410706  0.412579     857    344
95       95  0.404353   0.406661  0.408726     857    349
96       96  0.398847   0.401765  0.404346     857    329
97       97  0.391488   0.395346  0.398843     857    320
98       98  0.380012   0.386217  0.391469     857    325
99       99  0.332171   0.365994  0.380007     857    310
100     100  0.268624   0.312475  0.331878      99     37

[101 rows x 6 columns]

In [31]:
os.chdir('../Statistics/')

In [32]:
wb = load_workbook('report.xlsx')
writer = pd.ExcelWriter('report.xlsx',engine='openpyxl')
writer.book = wb
stats_numerical.to_excel(writer,sheet_name='ann_prob_stats',index=False)
writer.save()
writer.close()

In [14]:
os.chdir('../Input_Data')

In [15]:
df = pd.read_csv('oot.csv',header=0)

In [16]:
rename_dict = {col : col.replace('%','pct_') for col in df.columns if '%' in col}

In [17]:
df_val = df

In [18]:
df_val.rename(rename_dict,axis=1,inplace=True)

In [19]:
df_val['lift'] = df_val['actual_return'].apply(lambda x: 1 if x >0 else 0) 

In [20]:
for col in categorical:
    for category in conversion_dict[col]:
        df_val[col+'_dum_'+str(category)] = 0
        df_val.loc[df_val[col]==category,col+'_dum_'+str(category)]=1
    print(col+' done')

Sector done


In [21]:
rename_dict = {col : col.replace(' ','_').replace('-','_').replace('&','_') for col in df.columns if '-' in col or ' ' in col}

In [22]:
df_val.rename(rename_dict,axis=1,inplace=True)

In [23]:
for col in model_columns:
    df_val[col] = df_val[col].apply(lambda x : x if np.abs(x) <= 1 else np.sign(x)*1)

In [24]:
model.summary()

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_2 (InputLayer)         (None, 165)               0         
_________________________________________________________________
dense_4 (Dense)              (None, 85)                14110     
_________________________________________________________________
dense_5 (Dense)              (None, 85)                7310      
_________________________________________________________________
dense_6 (Dense)              (None, 1)                 86        
Total params: 21,506
Trainable params: 21,506
Non-trainable params: 0
_________________________________________________________________


In [25]:
def get_equation(model):
    mat1 = np.matrix(model.layers[1].get_weights()[0])
    mat2 = np.matrix(model.layers[1].get_weights()[1])
    mat3 = np.concatenate((mat1,mat2),axis=0)
    mat4 = np.matrix(model.layers[2].get_weights()[0])
    mat5 = np.matmul(mat3,mat4)
    mat5[165,:]+=np.matrix(model.layers[2].get_weights()[1])
    mat6 = np.matrix(model.layers[3].get_weights()[0])
    mat7 = np.matmul(mat5,mat6)
    mat7[165,:]+=np.matrix(model.layers[3].get_weights()[1])
    
    return [float(x) for x in mat7[:,0]]

In [26]:
dynamic_eqn = pd.DataFrame()
dynamic_eqn['Variable'] = list(model_columns)+['intercept']
dynamic_eqn['eq0'] = get_equation(model)

In [46]:
model.predict(np.array(model_inputs[56,:]).reshape(1,165))[0][0]

0.50779635

In [48]:
z = np.dot(np.array(list(model_inputs[56,:])+[1]),np.array(get_equation(model)))

In [51]:
np.exp(z)/(1+np.exp(z))

0.5077963458401455

In [27]:
dates = sorted(list(df_val['Date'].unique()))

In [28]:
os.chdir('../Models/')

In [29]:
model = load_model('ann_prob_model.h5')

In [30]:
ann_val_stats = pd.DataFrame()
for i,date in enumerate(dates):
    df_req = df_val[df_val['Date']==date]
    model_inputs = np.array(df_req[model_columns])
    model_returns = np.array(df_req['lift'])
    df_req['lift_prob'] = [x[0] for x in model.predict(model_inputs)]
    df_append = df_req[['Date','Symbol','Sector','lift','lift_prob']]
    ann_val_stats = ann_val_stats.append(df_append)
    model.fit(model_inputs,model_returns,batch_size=50,epochs=100)
    model.save('ann_prob_model.h5')
    model = load_model('ann_prob_model.h5')
    dynamic_eqn['eq'+str(i+1)] = get_equation(model)
    print('\n')
    print(dynamic_eqn)
    print('\n')
    print('{} days done'.format(i+1))
    print('\n')

C:\Users\DELL\Anaconda3\lib\site-packages\ipykernel_launcher.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  


Epoch 1/100
50/50 [==============================] - 0s 8ms/step - loss: 1.3845
Epoch 2/100
50/50 [==============================] - 0s 39us/step - loss: 1.3589
Epoch 3/100
50/50 [==============================] - 0s 40us/step - loss: 1.3120
Epoch 4/100
50/50 [==============================] - 0s 40us/step - loss: 1.2557
Epoch 5/100
50/50 [==============================] - 0s 60us/step - loss: 1.1979
Epoch 6/100
50/50 [==============================] - 0s 40us/step - loss: 1.1418
Epoch 7/100
50/50 [==============================] - 0s 40us/step - loss: 1.0869
Epoch 8/100
50/50 [==============================] - 0s 40us/step - loss: 1.0319
Epoch 9/100
50/50 [==============================] - 0s 40us/step - loss: 0.9762
Epoch 10/100
50/50 [==============================] - 0s 60us/step - loss: 0.9209
Epoch 11/100
50/50 [==============================] - 0s 40us/step - loss: 0.8682
Epoch 12/100
50/50 [==============================] - 0s 60us/step - loss: 0.8204
Epoch 13/100
50/50 [======



                              Variable        eq0        eq1
0                      High_pct_change  -3.469300  -6.782266
1                       Low_pct_change   0.628516  -1.876161
2                      Last_pct_change   9.972185   2.997030
3                      VWAP_pct_change   5.300334   0.238300
4                    Volume_pct_change  -0.119371   0.767334
5                  Turnover_pct_change   0.480565   1.064882
6                    Trades_pct_change  -1.349009  -4.034053
7        Deliverable_Volume_pct_change   1.514641   0.420047
8            pct_Deliverble_pct_change  -1.573479   0.136799
9                Open_nifty_pct_change   7.931855   4.486278
10               High_nifty_pct_change  -1.533139  -0.477832
11                Low_nifty_pct_change   8.269478   4.605814
12              Close_nifty_pct_change -10.112316  -5.864290
13             Volume_nifty_pct_change  -0.128230  -0.312751
14           Turnover_nifty_pct_change   0.505672   0.230467
15                Open

Epoch 55/100
50/50 [==============================] - 0s 80us/step - loss: 0.5936
Epoch 56/100
50/50 [==============================] - 0s 199us/step - loss: 0.5918
Epoch 57/100
50/50 [==============================] - 0s 40us/step - loss: 0.5900
Epoch 58/100
50/50 [==============================] - 0s 80us/step - loss: 0.5882
Epoch 59/100
50/50 [==============================] - 0s 60us/step - loss: 0.5863
Epoch 60/100
50/50 [==============================] - 0s 60us/step - loss: 0.5845
Epoch 61/100
50/50 [==============================] - 0s 40us/step - loss: 0.5827
Epoch 62/100
50/50 [==============================] - 0s 60us/step - loss: 0.5808
Epoch 63/100
50/50 [==============================] - 0s 80us/step - loss: 0.5790
Epoch 64/100
50/50 [==============================] - 0s 80us/step - loss: 0.5772
Epoch 65/100
50/50 [==============================] - 0s 100us/step - loss: 0.5754
Epoch 66/100
50/50 [==============================] - 0s 60us/step - loss: 0.5736
Epoch 67/100
5

50/50 [==============================] - 0s 5ms/step - loss: 1.1332
Epoch 2/100
50/50 [==============================] - 0s 60us/step - loss: 1.0449
Epoch 3/100
50/50 [==============================] - 0s 60us/step - loss: 0.9092
Epoch 4/100
50/50 [==============================] - 0s 60us/step - loss: 0.7657
Epoch 5/100
50/50 [==============================] - 0s 40us/step - loss: 0.6423
Epoch 6/100
50/50 [==============================] - 0s 60us/step - loss: 0.5527
Epoch 7/100
50/50 [==============================] - 0s 60us/step - loss: 0.4981
Epoch 8/100
50/50 [==============================] - 0s 60us/step - loss: 0.4723
Epoch 9/100
50/50 [==============================] - 0s 279us/step - loss: 0.4661
Epoch 10/100
50/50 [==============================] - 0s 60us/step - loss: 0.4710
Epoch 11/100
50/50 [==============================] - 0s 60us/step - loss: 0.4802
Epoch 12/100
50/50 [==============================] - 0s 60us/step - loss: 0.4892
Epoch 13/100
50/50 [=================

...

Epoch 100/100
50/50 [==============================] - 0s 299us/step - loss: 0.4305


                              Variable        eq0        eq1       eq2  \
0                      High_pct_change  -3.469300  -6.782266 -2.668533   
1                       Low_pct_change   0.628516  -1.876161 -3.184009   
2                      Last_pct_change   9.972185   2.997030 -1.977772   
3                      VWAP_pct_change   5.300334   0.238300 -2.253236   
4                    Volume_pct_change  -0.119371   0.767334  1.080417   
5                  Turnover_pct_change   0.480565   1.064882  0.860764   
6                    Trades_pct_change  -1.349009  -4.034053 -0.667788   
7        Deliverable_Volume_pct_change   1.514641   0.420047 -0.784645   
8            pct_Deliverble_pct_change  -1.573479   0.136799 -0.598269   
9                Open_nifty_pct_change   7.931855   4.486278  0.599835   
10               High_nifty_pct_change  -1.533139  -0.477832 -0.183796   
11                Low_nift

Epoch 1/100
50/50 [==============================] - 2s 30ms/step - loss: 0.8706
Epoch 2/100
50/50 [==============================] - 0s 299us/step - loss: 0.8624
Epoch 3/100
50/50 [==============================] - 0s 339us/step - loss: 0.8445
Epoch 4/100
50/50 [==============================] - 0s 459us/step - loss: 0.8210
Epoch 5/100
50/50 [==============================] - 0s 359us/step - loss: 0.7956
Epoch 6/100
50/50 [==============================] - 0s 419us/step - loss: 0.7710
Epoch 7/100
50/50 [==============================] - 0s 299us/step - loss: 0.7490
Epoch 8/100
50/50 [==============================] - 0s 299us/step - loss: 0.7304
Epoch 9/100
50/50 [==============================] - 0s 419us/step - loss: 0.7150
Epoch 10/100
50/50 [==============================] - 0s 419us/step - loss: 0.7021
Epoch 11/100
50/50 [==============================] - 0s 459us/step - loss: 0.6910
Epoch 12/100
50/50 [==============================] - 0s 439us/step - loss: 0.6808
Epoch 13/100
5

Epoch 100/100
50/50 [==============================] - 0s 259us/step - loss: 0.4345


                              Variable        eq0        eq1       eq2  \
0                      High_pct_change  -3.469300  -6.782266 -2.668533   
1                       Low_pct_change   0.628516  -1.876161 -3.184009   
2                      Last_pct_change   9.972185   2.997030 -1.977772   
3                      VWAP_pct_change   5.300334   0.238300 -2.253236   
4                    Volume_pct_change  -0.119371   0.767334  1.080417   
5                  Turnover_pct_change   0.480565   1.064882  0.860764   
6                    Trades_pct_change  -1.349009  -4.034053 -0.667788   
7        Deliverable_Volume_pct_change   1.514641   0.420047 -0.784645   
8            pct_Deliverble_pct_change  -1.573479   0.136799 -0.598269   
9                Open_nifty_pct_change   7.931855   4.486278  0.599835   
10               High_nifty_pct_change  -1.533139  -0.477832 -0.183796   
11                Low_nift

Epoch 1/100
50/50 [==============================] - 2s 32ms/step - loss: 1.3340
Epoch 2/100
50/50 [==============================] - 0s 279us/step - loss: 1.2754
Epoch 3/100
50/50 [==============================] - 0s 299us/step - loss: 1.1801
Epoch 4/100
50/50 [==============================] - 0s 239us/step - loss: 1.0784
Epoch 5/100
50/50 [==============================] - 0s 339us/step - loss: 0.9931
Epoch 6/100
50/50 [==============================] - 0s 299us/step - loss: 0.9338
Epoch 7/100
50/50 [==============================] - 0s 299us/step - loss: 0.8987
Epoch 8/100
50/50 [==============================] - 0s 299us/step - loss: 0.8791
Epoch 9/100
50/50 [==============================] - 0s 299us/step - loss: 0.8648
Epoch 10/100
50/50 [==============================] - 0s 299us/step - loss: 0.8485
Epoch 11/100
50/50 [==============================] - 0s 339us/step - loss: 0.8265
Epoch 12/100
50/50 [==============================] - 0s 339us/step - loss: 0.7984
Epoch 13/100
5

Epoch 100/100
50/50 [==============================] - 0s 299us/step - loss: 0.4402


                              Variable        eq0        eq1       eq2  \
0                      High_pct_change  -3.469300  -6.782266 -2.668533   
1                       Low_pct_change   0.628516  -1.876161 -3.184009   
2                      Last_pct_change   9.972185   2.997030 -1.977772   
3                      VWAP_pct_change   5.300334   0.238300 -2.253236   
4                    Volume_pct_change  -0.119371   0.767334  1.080417   
5                  Turnover_pct_change   0.480565   1.064882  0.860764   
6                    Trades_pct_change  -1.349009  -4.034053 -0.667788   
7        Deliverable_Volume_pct_change   1.514641   0.420047 -0.784645   
8            pct_Deliverble_pct_change  -1.573479   0.136799 -0.598269   
9                Open_nifty_pct_change   7.931855   4.486278  0.599835   
10               High_nifty_pct_change  -1.533139  -0.477832 -0.183796   
11                Low_nift

In [31]:
len(dates)

183

In [32]:
os.chdir('../Statistics/')

In [59]:
wb = load_workbook('report.xlsx')
writer = pd.ExcelWriter('report.xlsx',engine='openpyxl')
writer.book = wb
dynamic_eqn.to_excel(writer,sheet_name='ann_prob_dyn_eqn',index=False)
writer.save()
writer.close()

In [33]:
ann_val_stats['month'] = ann_val_stats['Date'].apply(lambda x : str(x)[5:7])
ann_val_stats['year'] = ann_val_stats['Date'].apply(lambda x: str(x)[0:4])

In [61]:
ann_val_stats

Date      Symbol                  Sector  lift  lift_prob month  \
0     2019-01-01  ADANIPORTS     Services - Shipping     1   0.466041    01   
62    2019-01-01  ASIANPAINT          Consumer Goods     0   0.490380    01   
124   2019-01-01    AXISBANK                 Banking     1   0.471869    01   
186   2019-01-01  BAJAJ-AUTO              Automobile     0   0.466816    01   
248   2019-01-01  BAJFINANCE      Financial Services     1   0.470475    01   
310   2019-01-01  BAJAJFINSV      Financial Services     1   0.469660    01   
372   2019-01-01  BHARTIARTL       Telecommunication     1   0.499124    01   
434   2019-01-01    INFRATEL       Telecommunication     1   0.504993    01   
496   2019-01-01        BPCL      Energy - Oil & Gas     1   0.468002    01   
558   2019-01-01   BRITANNIA          Consumer Goods     0   0.486802    01   
620   2019-01-01       CIPLA         Pharmaceuticals     1   0.455196    01   
682   2019-01-01   COALINDIA                  Metals     1   0.480304    01   
744   2019-01-01     DRREDDY         Pharmaceuticals     0   0.448060    01   
806   2019-01-01   EICHERMOT              Automobile     1   0.452775    01   
868   2019-01-01        GAIL      Energy - Oil & Gas     1   0.455438    01   
930   2019-01-01      GRASIM                  Cement     1   0.475633    01   
992   2019-01-01     HCLTECH  Information Technology     0   0.487278    01   
1054  2019-01-01        HDFC      Financial Services     1   0.472954    01   
1116  2019-01-01    HDFCBANK                 Banking     1   0.477864    01   
1178  2019-01-01  HEROMOTOCO              Automobile     1   0.463695    01   
1240  2019-01-01    HINDALCO                  Metals     0   0.443694    01   
1302  2019-01-01  HINDUNILVR          Consumer Goods     0   0.486516    01   
1364  2019-01-01   ICICIBANK                 Banking     1   0.480225    01   
1426  2019-01-01  IBULHSGFIN      Financial Services     0   0.465197    01   
1488  2019-01-01  INDUSINDBK                 Banking     0   0.468065    01   
1550  2019-01-01        INFY  Information Technology     1   0.494988    01   
1612  2019-01-01         IOC      Energy - Oil & Gas     1   0.461807    01   
1674  2019-01-01         ITC          Consumer Goods     1   0.495084    01   
1736  2019-01-01    JSWSTEEL                  Metals     0   0.442471    01   
1798  2019-01-01   KOTAKBANK                 Banking     0   0.467587    01   
...          ...         ...                     ...   ...        ...   ...   
1301  2019-03-29    HINDALCO                  Metals     0   0.228500    03   
1363  2019-03-29  HINDUNILVR          Consumer Goods     1   0.490343    03   
1425  2019-03-29   ICICIBANK                 Banking     0   0.777521    03   
1487  2019-03-29  IBULHSGFIN      Financial Services     1   0.952224    03   
1549  2019-03-29  INDUSINDBK                 Banking     0   0.904417    03   
1611  2019-03-29        INFY  Information Technology     0   0.878372    03   
1673  2019-03-29         IOC      Energy - Oil & Gas     0   0.212870    03   
1735  2019-03-29         ITC          Consumer Goods     0   0.395205    03   
1797  2019-03-29    JSWSTEEL                  Metals     1   0.071621    03   
1859  2019-03-29   KOTAKBANK                 Banking     0   0.749242    03   
1921  2019-03-29          LT            Construction     0   0.583851    03   
1983  2019-03-29         M&M              Automobile     1   0.169013    03   
2045  2019-03-29      MARUTI              Automobile     1   0.238026    03   
2107  2019-03-29        NTPC          Energy - Power     0   0.012810    03   
2169  2019-03-29        ONGC      Energy - Oil & Gas     1   0.092331    03   
2231  2019-03-29   POWERGRID          Energy - Power     0   0.011750    03   
2293  2019-03-29    RELIANCE      Energy - Oil & Gas     0   0.279781    03   
2355  2019-03-29        SBIN                 Banking     0   0.840477    03   
2417  2019-03-29   SUNPHARMA         Pharmaceuticals     1   0

In [38]:
ann_val_stats = ann_val_stats[(ann_val_stats['Date'] >= '2019-04-01') & (ann_val_stats['Date'] <= '2019-12-31')]

In [39]:
ann_val_grp1 = ann_val_stats.groupby(['month','year','Symbol','Sector']).apply(lambda group : roc_auc_score(y_true=group.lift,
                                                                                                           y_score=group.lift_prob))

In [40]:
ann_val_grp1

month  year  Symbol      Sector                
04     2019  ADANIPORTS  Services - Shipping       0.320513
             ASIANPAINT  Consumer Goods            0.556818
             AXISBANK    Banking                   0.600000
             BAJAJ-AUTO  Automobile                0.466667
             BAJAJFINSV  Financial Services        0.642857
             BAJFINANCE  Financial Services        0.454545
             BHARTIARTL  Telecommunication         0.611111
             BPCL        Energy - Oil & Gas        0.677778
             BRITANNIA   Consumer Goods            0.551282
             CIPLA       Pharmaceuticals           0.600000
             COALINDIA   Metals                    0.380952
             DRREDDY     Pharmaceuticals           0.625000
             EICHERMOT   Automobile                0.533333
             GAIL        Energy - Oil & Gas        0.677778
             GRASIM      Cement                    0.443182
             HCLTECH     Information Technology    0

In [41]:
ann_val_grp2 = ann_val_stats.groupby(['month','year','Symbol','Sector']).agg({'lift':['count','sum']})

In [42]:
ann_val_grp2

lift    
                                             count sum
month year Symbol     Sector                          
04    2019 ADANIPORTS Services - Shipping       19  13
           ASIANPAINT Consumer Goods            19   8
           AXISBANK   Banking                   19   4
           BAJAJ-AUTO Automobile                19   9
           BAJAJFINSV Financial Services        19  12
           BAJFINANCE Financial Services        19   8
           BHARTIARTL Telecommunication         19   9
           BPCL       Energy - Oil & Gas        19   9
           BRITANNIA  Consumer Goods            19   6
           CIPLA      Pharmaceuticals           19   9
           COALINDIA  Metals                    19   7
           DRREDDY    Pharmaceuticals           19   8
           EICHERMOT  Automobile                19   9
           GAIL       Energy - Oil & Gas        19  10
           GRASIM     Cement                    19  11
           HCLTECH    Information Technology    19   8
           HDFC       Financial Services        19  10
           HDFCBANK   Banking                   19   9
           HEROMOTOCO Automobile                19   7
           HINDALCO   Metals                    19  11
           HINDUNILVR Consumer Goods            19  10
           IBULHSGFIN Financial Services        19   5
           ICICIBANK  Banking                   19   7
           INDUSINDBK Banking                   19   7
           INFRATEL   Telecommunication         19   7
           INFY       Information Technology    19  11
           IOC        Energy - Oil & Gas        19   9
           ITC        Consumer Goods            19   8
           JSWSTEEL   Metals                    19   7
           KOTAKBANK  Banking                   19  11
...                                            ...  ..
12    2019 HINDUNILVR Consumer Goods            21   6
           IBULHSGFIN Financial Services        21   9
           ICICIBANK  Banking                   21   9
           INDUSINDBK Banking                   21   8
           INFRATEL   Telecommunication         21   8
           INFY       Information Technology    21  14
           IOC        Energy - Oil & Gas        21   9
           ITC        Consumer Goods            21   7
           JSWSTEEL   Metals                    21  13
           KOTAKBANK  Banking                   21  12
           LT         Construction              21   9
           M&M        Automobile                21  10
           MARUTI     Automobile                21   6
           NTPC       Energy - Power            21  11
           ONGC       Energy - Oil & Gas        21   8
           POWERGRID  Energy - Power            21  11
           RELIANCE   Energy - Oil & Gas        21   8
           SBIN       Banking                   21   7
           SUNPHARMA  Pharmaceuticals           21  12
           TATAMOTORS Automobile                21   9
           TATASTEEL  Metals                    21  14
           TCS        Information Technology    21  10
           TECHM      Information Technology    21   8
           TITAN      Consumer Goods            21  10
           ULTRACEMCO Cement                    21   4
           UPL        Chemicals                 21   8
           VEDL       Metals                    21  10
           WIPRO      Information Technology    21  11
           YESBANK    Banking                   21   8
           ZEEL       Media & Entertainment     21  11

[450 rows x 2 columns]

In [43]:
ann_val_grp = pd.DataFrame(ann_val_grp1).join(ann_val_grp2)

C:\Users\DELL\Anaconda3\lib\site-packages\pandas\core\reshape\merge.py:543: UserWarning: merging between different levels can give an unintended result (1 levels on the left, 2 on the right)
  warnings.warn(msg, UserWarning)


In [44]:
ann_val_grp.columns = ['roc_auc_score','trade days','lifts']

In [45]:
ann_val_grp = ann_val_grp[['trade days','lifts','roc_auc_score']]

In [46]:
ann_val_grp.reset_index(inplace=True)

In [47]:
ann_val_grp.shape

(450, 7)

In [87]:
os.getcwd()

'C:\\Users\\DELL\\Desktop\\Trading App\\Revised_Investing\\Trading App_v02\\Price Prediction\\Statistics'

In [48]:
wb = load_workbook('report.xlsx')
writer = pd.ExcelWriter('report.xlsx',engine='openpyxl')
writer.book = wb
ann_val_grp.to_excel(writer,sheet_name='ann_prob_oot_stats',index=False)
writer.save()
writer.close()

In [49]:
os.chdir('../Models/')

In [50]:
model.save('ann_prob_model.h5')